In [1]:
import findspark
findspark.init()
import pandas as pd
from pyspark import SparkConf, SparkContext
import os
import re
import time
import datetime
import random

conf = SparkConf()
sc = SparkContext.getOrCreate(conf=conf)

In [2]:
user_clicklist = sc.textFile('./user_clicklist_test_final')\
                .map(lambda line: tuple(re.findall(r"'(.*?)'", line)))\
                .map(lambda info: (info[0] + '|' + info[1], (info[2:])))

print(user_clicklist.take(1))
print(user_clicklist.count())

[('7fd3eaa2-5d74-4000-bf1a-17bcec21ad5d|US', ('2210170', '1095341', '1084306', '2226356', '2209940', '772737', '1271388', '2212919', '2216160', '2217438', '300456', '2209719', '2209268', '1375111', '763794', '2221161', '1204234', '1359886', '2222048'))]
7123


In [3]:
import json
with open('user_feature_subsample.json') as json_file:  
    user_subsample = json.load(json_file)

In [4]:
# val and test split
user_clicklist_split = user_clicklist.map(lambda info: (info[0].split('|')[0],  info[1], random.getrandbits(1)))\
                        .filter(lambda info: info[0] in user_subsample)

user_clicklist_val = user_clicklist_split.filter(lambda info: info[2] == 1)
user_clicklist_test = user_clicklist_split.filter(lambda info: info[2] == 0)

print(user_clicklist_split.take(3))
print(user_clicklist_val.count())
print(user_clicklist_test.count())

[('8b73ac00-701e-4396-9d99-4bef1928b206', ('300456', '2210788', '682642', '1135496', '1183493', '2211288', '2218375', '2200730', '1344565', '2209940', '2213614', '2211486', '2218701'), 1), ('fec476acc9411c38', ('105808', '111377', '981215', '982391', '108658', '981443', '981550', '114555', '107058', '300456', '979708', '981748', '981890', '980612', '979481', '981899', '89927', '983100', '984933', '984545', '111858', '109778', '110122', '93634', '300456', '979936', '984114', '986216', '983915', '990618', '97560', '991107', '988982', '988314', '985183', '991110', '300456', '989800', '990296', '81206', '983117'), 1), ('e06fb43d-f514-42dc-9c4b-f1f25101f55e', ('715619', '2223081', '2210029', '632888', '740078', '2224362', '2218259', '682642', '1264192', '1193291', '2211299', '2223149', '300456', '2207761', '2214135', '2207449', '2213447', '803744', '1249135', '986153', '2210761', '2210363', '1204750', '763794', '687849', '2221778', '820057', '2207887', '966404', '584031', '2187657', '221508

In [5]:
def to_string_list(t):
    l = list(t)
    return ",".join(l)

user_clicklist_val_output = user_clicklist_val.map(lambda x: (x[0], to_string_list(x[1])))
user_clicklist_test_output = user_clicklist_test.map(lambda x: (x[0], to_string_list(x[1])))


print(user_clicklist_val_output.take(3))

print(user_clicklist_test_output.take(3))

[('8b73ac00-701e-4396-9d99-4bef1928b206', '300456,2210788,682642,1135496,1183493,2211288,2218375,2200730,1344565,2209940,2213614,2211486,2218701'), ('344e1638-83e7-4eab-9716-a747a94d58c6', '2210988,2223933,2213331,2221648,1231743,1156020,2213689,2207646,387976,2208440,1072039,2218324,2219026'), ('ebdb4859-8802-465f-aa4d-1d8686fffce7', '2215604,512478,2216346,2214362,2212553,2220219,2219296,2212305,449447,2216442,2213243,2220370,2219921,2218864,2218626,2218384,959871,578364,2212160,2220995,2211595,2217258,2219771,2215623,2208402')]
[('fec476acc9411c38', '105808,111377,981215,982391,108658,981443,981550,114555,107058,300456,979708,981748,981890,980612,979481,981899,89927,983100,984933,984545,111858,109778,110122,93634,300456,979936,984114,986216,983915,990618,97560,991107,988982,988314,985183,991110,300456,989800,990296,81206,983117'), ('deade3cb-0c5e-4913-8dd6-5217bc510765', '2223081,2223428,2217943,2214829,2214362,2207646,1223361,1083556,2213689,2221493,2214132,2196467,2223827,2208402,

In [6]:
from pyspark.sql.types import Row
from pyspark.sql import SparkSession
from pyspark import SparkContext


spark = SparkSession(sc)

#Now populate that
df_val = user_clicklist_val_output.toDF()
df_test = user_clicklist_test_output.toDF()

In [7]:
df_val.show(1)
df_test.show(1)

+--------------------+--------------------+
|                  _1|                  _2|
+--------------------+--------------------+
|e06fb43d-f514-42d...|715619,2223081,22...|
+--------------------+--------------------+
only showing top 1 row

+--------------------+--------------------+
|                  _1|                  _2|
+--------------------+--------------------+
|8b73ac00-701e-439...|300456,2210788,68...|
+--------------------+--------------------+
only showing top 1 row



In [8]:
df_val.write.csv('user_clicklist_val_user_subsample')

df_test.write.csv('user_clicklist_test_user_subsample')

In [16]:
# save click list in training

user_clicklist = sc.textFile('./user_clicklist_train_final')\
                .map(lambda line: tuple(re.findall(r"'(.*?)'", line)))\
                .map(lambda info: (info[0] + '|' + info[1], (info[2:])))

print(user_clicklist.take(1))
print(user_clicklist.count())

[('122b7665-6fac-4278-97e8-b72f7ccbb5dc|CA', ('1204234', '1279326', '1303559', '1303095', '1294468', '1291345', '1294630', '1300744', '1306010', '1297366', '1306464', '1300534', '1292887', '1304703', '1252819', '1304914', '1302796', '835561', '1306111', '1303479', '1294018', '1306502', '571314', '1230406', '1297326', '1266919', '1319968', '1321695', '822793', '1320028', '1324974', '1316488', '1311850', '1316835', '1231743', '1320001', '1316364', '1252819', '1315364', '1316381', '1310291', '1313806', '1314249', '1311329', '1311003', '1325428', '1316363', '716627', '1253223', '1319976', '1328614', '1248217', '1350109', '1346601', '559815', '1213333', '59859', '1350476', '1327102', '722391', '1327941', '1307546', '1334790', '1306535', '1327545', '1327641', '1326167', '1349870', '1234020', '1341232', '1350470', '1342615', '1348048', '1347829', '739076', '1344368', '1343083', '715619', '1344061', '1341736', '1341574', '1339778', '1047306', '1351678', '1339322', '1183115', '1084445', '135559

In [17]:
def to_string_list(t):
    l = list(t)
    return ",".join(l)

user_clicklist_train_output = user_clicklist.map(lambda x: (x[0].split('|')[0], to_string_list(x[1])))


print(user_clicklist_train_output.take(3))

[('122b7665-6fac-4278-97e8-b72f7ccbb5dc', '1204234,1279326,1303559,1303095,1294468,1291345,1294630,1300744,1306010,1297366,1306464,1300534,1292887,1304703,1252819,1304914,1302796,835561,1306111,1303479,1294018,1306502,571314,1230406,1297326,1266919,1319968,1321695,822793,1320028,1324974,1316488,1311850,1316835,1231743,1320001,1316364,1252819,1315364,1316381,1310291,1313806,1314249,1311329,1311003,1325428,1316363,716627,1253223,1319976,1328614,1248217,1350109,1346601,559815,1213333,59859,1350476,1327102,722391,1327941,1307546,1334790,1306535,1327545,1327641,1326167,1349870,1234020,1341232,1350470,1342615,1348048,1347829,739076,1344368,1343083,715619,1344061,1341736,1341574,1339778,1047306,1351678,1339322,1183115,1084445,1355593,1351373,1231743,1352740,1365661,1313677,1101575,1365638,1362224,1356876,1355482,1349079,1111397,1355977,1356630,1354289,1203204,1358881,1354956,1355602,693327,1360003,1362381,1361135,1355044,1393578,1386296,1392428,1397367,1389101,1396123,1399561,1390826,1388539,

In [18]:
from pyspark.sql.types import Row
from pyspark.sql import SparkSession
from pyspark import SparkContext


spark = SparkSession(sc)

#Now populate that
df_train = user_clicklist_train_output.toDF()

In [20]:
df_train.write.csv('user_clicklist_train')

In [3]:
# save user feature into csv
if not os.path.isfile('./user_feature'):
    !gsutil -m cp gs://dataproc-8a63ee66-417e-4e10-b748-8ad7b3f18436-us/user_feature ./user_feature
user_feature = sc.textFile('./user_feature').map(lambda line: line.replace('(', ''))\
                .map(lambda line: line.replace(')', ''))\
                .map(lambda line: line.split(', '))\
                .map(lambda line: (line[0].replace("'", ""), line[1:]))\
                .reduceByKey(lambda line1, line2: line1)\
                .map(lambda line: ((line[0], ) + (1553904000.0, ) + tuple(line[1][:14]) + tuple(line[1][14:])))

print(user_feature.take(1))
print(user_feature.count())

[('64a6382b-9e59-4767-95fa-fa4ef2910675', 1553904000.0, '0.0', '1.0', '0.0', '0.0', '0.0', '0.0', '0.0', '0.0', '0.0', '0.0', '0.0', '0.0', '0.0', '0.0', '0.0070921985815602835', '0.02127659574468085', '0.2553191489361702', '0.02127659574468085', '0.06382978723404255', '0.0', '0.028368794326241134', '0.02127659574468085', '0.0425531914893617', '0.0070921985815602835', '0.0', '0.0', '0.02127659574468085', '0.02127659574468085', '0.028368794326241134', '0.03546099290780142', '0.0', '0.02127659574468085', '0.0', '0.02127659574468085', '0.04964539007092199', '0.03546099290780142', '0.0070921985815602835', '0.02127659574468085', '0.0', '0.014184397163120567', '0.0', '0.0', '0.02127659574468085', '0.03546099290780142', '0.04964539007092199', '0.0', '0.0', '0.0070921985815602835', '0.0', '0.0', '0.028368794326241134', '0.0', '0.0', '0.0', '0.0', '0.0', '0.0', '0.0070921985815602835', '0.0070921985815602835', '0.014184397163120567', '0.0070921985815602835', '0.04964539007092199', '0.0', '0.028

In [5]:
from pyspark.sql.types import Row
from pyspark.sql import SparkSession
from pyspark import SparkContext


spark = SparkSession(sc)

def f(x):
    d = tuple()
    for i in range(len(x)):
        if i == 0:
            d += (x[i],)
        else:
            d += (float(x[i]),)
    return d

#Now populate that
df = user_feature.map(lambda x: f(x)).toDF()
df.show(1)

+--------------------+----------+---+---+---+---+---+---+---+---+---+---+---+---+---+---+--------------------+-------------------+------------------+-------------------+-------------------+---+--------------------+-------------------+------------------+--------------------+---+---+-------------------+-------------------+--------------------+-------------------+---+-------------------+---+-------------------+-------------------+-------------------+--------------------+-------------------+---+--------------------+---+---+-------------------+-------------------+-------------------+---+---+--------------------+---+---+--------------------+---+---+---+---+---+---+--------------------+--------------------+--------------------+--------------------+-------------------+---+--------------------+
|                  _1|        _2| _3| _4| _5| _6| _7| _8| _9|_10|_11|_12|_13|_14|_15|_16|                 _17|                _18|               _19|                _20|                _21|_22|          

In [7]:
df.write.csv('user_feature_val_test')

In [4]:
# generate candidate post feature
user_clicklist_train = sc.textFile('./user_clicklist_train_final')\
                .map(lambda line: tuple(re.findall(r"'(.*?)'", line)))\
                .map(lambda info: (info[0] + '|' + info[1], (info[2:])))

user_clicklist_test = sc.textFile('./user_clicklist_test_final')\
                .map(lambda line: tuple(re.findall(r"'(.*?)'", line)))\
                .map(lambda info: (info[0] + '|' + info[1], (info[2:])))

print(user_clicklist_train.take(1))
print(user_clicklist_test.take(1))

[('122b7665-6fac-4278-97e8-b72f7ccbb5dc|CA', ('1204234', '1279326', '1303559', '1303095', '1294468', '1291345', '1294630', '1300744', '1306010', '1297366', '1306464', '1300534', '1292887', '1304703', '1252819', '1304914', '1302796', '835561', '1306111', '1303479', '1294018', '1306502', '571314', '1230406', '1297326', '1266919', '1319968', '1321695', '822793', '1320028', '1324974', '1316488', '1311850', '1316835', '1231743', '1320001', '1316364', '1252819', '1315364', '1316381', '1310291', '1313806', '1314249', '1311329', '1311003', '1325428', '1316363', '716627', '1253223', '1319976', '1328614', '1248217', '1350109', '1346601', '559815', '1213333', '59859', '1350476', '1327102', '722391', '1327941', '1307546', '1334790', '1306535', '1327545', '1327641', '1326167', '1349870', '1234020', '1341232', '1350470', '1342615', '1348048', '1347829', '739076', '1344368', '1343083', '715619', '1344061', '1341736', '1341574', '1339778', '1047306', '1351678', '1339322', '1183115', '1084445', '135559

In [5]:
# combine train and test clicklist
user_clicklist = user_clicklist_train.union(user_clicklist_test).reduceByKey(lambda x1, x2: x1 + x2)

print(user_clicklist.take(1))
print(user_clicklist.count())


[('3597d5b5-01f2-44c4-ae34-d6279970e569|GB', ('1268347', '1297829', '1293070', '1295562', '1287213', '1302627', '1294332', '1296589', '1168912', '1297834', '1296767', '1299417', '1306010', '1302619', '1294350', '1294468', '1283659', '1067073', '1294140', '1204234', '1310068', '1319311', '1311913', '1315364', '1316145', '1323764', '1313436', '1310910', '1306010', '1310606', '1311699', '1310577', '1316364', '1319273', '1322011', '1316363', '1322771', '1323565', '1322292', '1322923', '600580', '1322340', '1287242', '1319394', '1324116', '1322024', '1354479', '1395578', '1377294', '1396814', '1394080', '1382649', '1394216', '1396123', '1393790', '1379588', '1396800', '1415072', '1416598', '424992', '1370260', '1414128', '1416632', '1421021', '1413323', '1231743', '715375', '2189928', '2189903', '1411309', '1316626', '2189710', '1369692', '1423565', '1416724', '2198278', '2198182', '1220679', '410779', '2190074', '2194926', '2196601', '857137', '1258062', '2207887', '2203597', '2199227', '2

In [6]:
# post feature dict

if not os.path.isfile('./post_feature_2018'):
    !gsutil -m cp gs://dataproc-8a63ee66-417e-4e10-b748-8ad7b3f18436-us/post_feature_2018 ./post_feature_2018
post_feature = sc.textFile('./post_feature_2018')

post_feature = post_feature.map(lambda line: line.replace('(', ''))\
                .map(lambda line: line.replace(')', ''))\
                .map(lambda line: line.split(', '))\
                .map(lambda line: (line[0].replace("'", ""), line[1:]))

print(post_feature.take(1))

post_feature_dict = post_feature.collectAsMap()

[('1002075', ['0.006635333', '-0.059507362', '-0.24372492', '0.199611793', '-0.295117519', '-0.235775492', '0.370891783', '0.15483705', '-0.199782611', '0.141436241', '-0.059329205', '0.014627483', '0.017688913', '0.129799746', '-0.322009452', '0.117001533', '-0.157055944', '-0.156147639', '-0.026699203', '-0.083844235', '0.064606814', '0.140012898', '-0.017496294', '0.19904785', '0.192821605', '0.30772681', '-0.100998803', '0.111794012', '-0.043496373', '-0.156214913', '-0.26270495', '-0.156135275', '41.0', '1554249600.0'])]


In [7]:
clicked_post = user_clicklist.flatMap(lambda x: x[1]).distinct().filter(lambda x: post_feature_dict.get(x) != None)\
                .map(lambda x: (x, post_feature_dict.get(x)))

print(clicked_post.count())
print(clicked_post.take(10))

71250
[('1411156', ['-0.457786795', '0.137379635', '0.07698243', '-0.110999753', '0.084061611', '-0.051000468', '0.072448008', '0.262698545', '0.091256308', '0.170169595', '-0.095170692', '-0.062520205', '-0.027281829', '-0.085082479', '-0.456151987', '-0.118537325', '-0.239420263', '0.073112657', '-0.240651439', '0.07986596', '0.14119256', '0.109851583', '0.245301634', '0.158016653', '0.009866226', '0.155387121', '-0.058666536', '0.014276422', '-0.142516665', '-0.132752822', '0.083471258', '-0.268569525', '2.0', '1532476800.0']), ('1064240', ['-0.037902765', '0.05906328', '0.084977856', '0.269107294', '0.097783326', '0.007888006', '-0.085366733', '0.268626085', '0.330555106', '0.351523229', '0.021653645', '0.050141462', '-0.164294776', '0.219981938', '-0.449907652', '-0.138022204', '0.031837783', '-0.015394243', '0.039234855', '0.150281376', '-0.086177801', '-0.183152107', '-0.017877345', '-0.011364496', '0.066998751', '0.398558197', '-0.004625322', '-0.020376823', '-0.130850629', '0.

In [19]:
post_feature = clicked_post.map(lambda x: (x[1][-2],) + (x[0], ) + tuple(x[1][:-2]) + (x[1][-1], )).collect()

print(post_feature[0])

('3.0', '1227963', '-0.263193485', '0.040504625', '-0.077210643', '0.376023312', '-0.126799685', '0.292204925', '-0.057926305', '0.160891639', '-0.101574483', '0.088706719', '0.219812377', '0.041306027', '0.045448225', '0.18278806', '-0.096411438', '0.201370577', '-0.208626641', '0.154250852', '-0.024330153', '-0.263783538', '-0.121470101', '0.037513885', '0.121071604', '-0.061459715', '0.070752093', '-0.012086583', '0.027024085', '0.506861724', '-0.107107484', '-0.054583098', '0.213862325', '-0.049278643', '1518307200.0')


In [35]:
print(post_feature[0][1])
clusters = {}
i = 0
for post in post_feature:
    if post[0] in clusters:
        cluster = clusters[post[0]]
        cluster[post[1]] = list(post[2:])
    else:
        cluster = {}
        cluster[post[1]] = list(post[2:])
        clusters[post[0]] = cluster
    print(i)
    i += 1


1227963
0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99
100
101
102
103
104
105
106
107
108
109
110
111
112
113
114
115
116
117
118
119
120
121
122
123
124
125
126
127
128
129
130
131
132
133
134
135
136
137
138
139
140
141
142
143
144
145
146
147
148
149
150
151
152
153
154
155
156
157
158
159
160
161
162
163
164
165
166
167
168
169
170
171
172
173
174
175
176
177
178
179
180
181
182
183
184
185
186
187
188
189
190
191
192
193
194
195
196
197
198
199
200
201
202
203
204
205
206
207
208
209
210
211
212
213
214
215
216
217
218
219
220
221
222
223
224
225
226
227
228
229
230
231
232
233
234
235
236
237
238
239
240
241
242
243
244
245
246
247
248
249
250
251
252
253
254
255
256
257
258
259
260
261
262
263
264
265
266
267
268
269
270
271
272
273
274
27

2930
2931
2932
2933
2934
2935
2936
2937
2938
2939
2940
2941
2942
2943
2944
2945
2946
2947
2948
2949
2950
2951
2952
2953
2954
2955
2956
2957
2958
2959
2960
2961
2962
2963
2964
2965
2966
2967
2968
2969
2970
2971
2972
2973
2974
2975
2976
2977
2978
2979
2980
2981
2982
2983
2984
2985
2986
2987
2988
2989
2990
2991
2992
2993
2994
2995
2996
2997
2998
2999
3000
3001
3002
3003
3004
3005
3006
3007
3008
3009
3010
3011
3012
3013
3014
3015
3016
3017
3018
3019
3020
3021
3022
3023
3024
3025
3026
3027
3028
3029
3030
3031
3032
3033
3034
3035
3036
3037
3038
3039
3040
3041
3042
3043
3044
3045
3046
3047
3048
3049
3050
3051
3052
3053
3054
3055
3056
3057
3058
3059
3060
3061
3062
3063
3064
3065
3066
3067
3068
3069
3070
3071
3072
3073
3074
3075
3076
3077
3078
3079
3080
3081
3082
3083
3084
3085
3086
3087
3088
3089
3090
3091
3092
3093
3094
3095
3096
3097
3098
3099
3100
3101
3102
3103
3104
3105
3106
3107
3108
3109
3110
3111
3112
3113
3114
3115
3116
3117
3118
3119
3120
3121
3122
3123
3124
3125
3126
3127
3128
3129


5901
5902
5903
5904
5905
5906
5907
5908
5909
5910
5911
5912
5913
5914
5915
5916
5917
5918
5919
5920
5921
5922
5923
5924
5925
5926
5927
5928
5929
5930
5931
5932
5933
5934
5935
5936
5937
5938
5939
5940
5941
5942
5943
5944
5945
5946
5947
5948
5949
5950
5951
5952
5953
5954
5955
5956
5957
5958
5959
5960
5961
5962
5963
5964
5965
5966
5967
5968
5969
5970
5971
5972
5973
5974
5975
5976
5977
5978
5979
5980
5981
5982
5983
5984
5985
5986
5987
5988
5989
5990
5991
5992
5993
5994
5995
5996
5997
5998
5999
6000
6001
6002
6003
6004
6005
6006
6007
6008
6009
6010
6011
6012
6013
6014
6015
6016
6017
6018
6019
6020
6021
6022
6023
6024
6025
6026
6027
6028
6029
6030
6031
6032
6033
6034
6035
6036
6037
6038
6039
6040
6041
6042
6043
6044
6045
6046
6047
6048
6049
6050
6051
6052
6053
6054
6055
6056
6057
6058
6059
6060
6061
6062
6063
6064
6065
6066
6067
6068
6069
6070
6071
6072
6073
6074
6075
6076
6077
6078
6079
6080
6081
6082
6083
6084
6085
6086
6087
6088
6089
6090
6091
6092
6093
6094
6095
6096
6097
6098
6099
6100


8498
8499
8500
8501
8502
8503
8504
8505
8506
8507
8508
8509
8510
8511
8512
8513
8514
8515
8516
8517
8518
8519
8520
8521
8522
8523
8524
8525
8526
8527
8528
8529
8530
8531
8532
8533
8534
8535
8536
8537
8538
8539
8540
8541
8542
8543
8544
8545
8546
8547
8548
8549
8550
8551
8552
8553
8554
8555
8556
8557
8558
8559
8560
8561
8562
8563
8564
8565
8566
8567
8568
8569
8570
8571
8572
8573
8574
8575
8576
8577
8578
8579
8580
8581
8582
8583
8584
8585
8586
8587
8588
8589
8590
8591
8592
8593
8594
8595
8596
8597
8598
8599
8600
8601
8602
8603
8604
8605
8606
8607
8608
8609
8610
8611
8612
8613
8614
8615
8616
8617
8618
8619
8620
8621
8622
8623
8624
8625
8626
8627
8628
8629
8630
8631
8632
8633
8634
8635
8636
8637
8638
8639
8640
8641
8642
8643
8644
8645
8646
8647
8648
8649
8650
8651
8652
8653
8654
8655
8656
8657
8658
8659
8660
8661
8662
8663
8664
8665
8666
8667
8668
8669
8670
8671
8672
8673
8674
8675
8676
8677
8678
8679
8680
8681
8682
8683
8684
8685
8686
8687
8688
8689
8690
8691
8692
8693
8694
8695
8696
8697


11173
11174
11175
11176
11177
11178
11179
11180
11181
11182
11183
11184
11185
11186
11187
11188
11189
11190
11191
11192
11193
11194
11195
11196
11197
11198
11199
11200
11201
11202
11203
11204
11205
11206
11207
11208
11209
11210
11211
11212
11213
11214
11215
11216
11217
11218
11219
11220
11221
11222
11223
11224
11225
11226
11227
11228
11229
11230
11231
11232
11233
11234
11235
11236
11237
11238
11239
11240
11241
11242
11243
11244
11245
11246
11247
11248
11249
11250
11251
11252
11253
11254
11255
11256
11257
11258
11259
11260
11261
11262
11263
11264
11265
11266
11267
11268
11269
11270
11271
11272
11273
11274
11275
11276
11277
11278
11279
11280
11281
11282
11283
11284
11285
11286
11287
11288
11289
11290
11291
11292
11293
11294
11295
11296
11297
11298
11299
11300
11301
11302
11303
11304
11305
11306
11307
11308
11309
11310
11311
11312
11313
11314
11315
11316
11317
11318
11319
11320
11321
11322
11323
11324
11325
11326
11327
11328
11329
11330
11331
11332
11333
11334
11335
11336
11337
11338
1133

...

59598
59599
59600
59601
59602
59603
59604
59605
59606
59607
59608
59609
59610
59611
59612
59613
59614
59615
59616
59617
59618
59619
59620
59621
59622
59623
59624
59625
59626
59627
59628
59629
59630
59631
59632
59633
59634
59635
59636
59637
59638
59639
59640
59641
59642
59643
59644
59645
59646
59647
59648
59649
59650
59651
59652
59653
59654
59655
59656
59657
59658
59659
59660
59661
59662
59663
59664
59665
59666
59667
59668
59669
59670
59671
59672
59673
59674
59675
59676
59677
59678
59679
59680
59681
59682
59683
59684
59685
59686
59687
59688
59689
59690
59691
59692
59693
59694
59695
59696
59697
59698
59699
59700
59701
59702
59703
59704
59705
59706
59707
59708
59709
59710
59711
59712
59713
59714
59715
59716
59717
59718
59719
59720
59721
59722
59723
59724
59725
59726
59727
59728
59729
59730
59731
59732
59733
59734
59735
59736
59737
59738
59739
59740
59741
59742
59743
59744
59745
59746
59747
59748
59749
59750
59751
59752
59753
59754
59755
59756
59757
59758
59759
59760
59761
59762
59763
5976

61684
61685
61686
61687
61688
61689
61690
61691
61692
61693
61694
61695
61696
61697
61698
61699
61700
61701
61702
61703
61704
61705
61706
61707
61708
61709
61710
61711
61712
61713
61714
61715
61716
61717
61718
61719
61720
61721
61722
61723
61724
61725
61726
61727
61728
61729
61730
61731
61732
61733
61734
61735
61736
61737
61738
61739
61740
61741
61742
61743
61744
61745
61746
61747
61748
61749
61750
61751
61752
61753
61754
61755
61756
61757
61758
61759
61760
61761
61762
61763
61764
61765
61766
61767
61768
61769
61770
61771
61772
61773
61774
61775
61776
61777
61778
61779
61780
61781
61782
61783
61784
61785
61786
61787
61788
61789
61790
61791
61792
61793
61794
61795
61796
61797
61798
61799
61800
61801
61802
61803
61804
61805
61806
61807
61808
61809
61810
61811
61812
61813
61814
61815
61816
61817
61818
61819
61820
61821
61822
61823
61824
61825
61826
61827
61828
61829
61830
61831
61832
61833
61834
61835
61836
61837
61838
61839
61840
61841
61842
61843
61844
61845
61846
61847
61848
61849
6185

64304
64305
64306
64307
64308
64309
64310
64311
64312
64313
64314
64315
64316
64317
64318
64319
64320
64321
64322
64323
64324
64325
64326
64327
64328
64329
64330
64331
64332
64333
64334
64335
64336
64337
64338
64339
64340
64341
64342
64343
64344
64345
64346
64347
64348
64349
64350
64351
64352
64353
64354
64355
64356
64357
64358
64359
64360
64361
64362
64363
64364
64365
64366
64367
64368
64369
64370
64371
64372
64373
64374
64375
64376
64377
64378
64379
64380
64381
64382
64383
64384
64385
64386
64387
64388
64389
64390
64391
64392
64393
64394
64395
64396
64397
64398
64399
64400
64401
64402
64403
64404
64405
64406
64407
64408
64409
64410
64411
64412
64413
64414
64415
64416
64417
64418
64419
64420
64421
64422
64423
64424
64425
64426
64427
64428
64429
64430
64431
64432
64433
64434
64435
64436
64437
64438
64439
64440
64441
64442
64443
64444
64445
64446
64447
64448
64449
64450
64451
64452
64453
64454
64455
64456
64457
64458
64459
64460
64461
64462
64463
64464
64465
64466
64467
64468
64469
6447

66667
66668
66669
66670
66671
66672
66673
66674
66675
66676
66677
66678
66679
66680
66681
66682
66683
66684
66685
66686
66687
66688
66689
66690
66691
66692
66693
66694
66695
66696
66697
66698
66699
66700
66701
66702
66703
66704
66705
66706
66707
66708
66709
66710
66711
66712
66713
66714
66715
66716
66717
66718
66719
66720
66721
66722
66723
66724
66725
66726
66727
66728
66729
66730
66731
66732
66733
66734
66735
66736
66737
66738
66739
66740
66741
66742
66743
66744
66745
66746
66747
66748
66749
66750
66751
66752
66753
66754
66755
66756
66757
66758
66759
66760
66761
66762
66763
66764
66765
66766
66767
66768
66769
66770
66771
66772
66773
66774
66775
66776
66777
66778
66779
66780
66781
66782
66783
66784
66785
66786
66787
66788
66789
66790
66791
66792
66793
66794
66795
66796
66797
66798
66799
66800
66801
66802
66803
66804
66805
66806
66807
66808
66809
66810
66811
66812
66813
66814
66815
66816
66817
66818
66819
66820
66821
66822
66823
66824
66825
66826
66827
66828
66829
66830
66831
66832
6683

69018
69019
69020
69021
69022
69023
69024
69025
69026
69027
69028
69029
69030
69031
69032
69033
69034
69035
69036
69037
69038
69039
69040
69041
69042
69043
69044
69045
69046
69047
69048
69049
69050
69051
69052
69053
69054
69055
69056
69057
69058
69059
69060
69061
69062
69063
69064
69065
69066
69067
69068
69069
69070
69071
69072
69073
69074
69075
69076
69077
69078
69079
69080
69081
69082
69083
69084
69085
69086
69087
69088
69089
69090
69091
69092
69093
69094
69095
69096
69097
69098
69099
69100
69101
69102
69103
69104
69105
69106
69107
69108
69109
69110
69111
69112
69113
69114
69115
69116
69117
69118
69119
69120
69121
69122
69123
69124
69125
69126
69127
69128
69129
69130
69131
69132
69133
69134
69135
69136
69137
69138
69139
69140
69141
69142
69143
69144
69145
69146
69147
69148
69149
69150
69151
69152
69153
69154
69155
69156
69157
69158
69159
69160
69161
69162
69163
69164
69165
69166
69167
69168
69169
69170
69171
69172
69173
69174
69175
69176
69177
69178
69179
69180
69181
69182
69183
6918

In [36]:
import json

with open('post_feature.txt', 'w') as outfile:  
    json.dump(clusters, outfile)

In [40]:

with open('post_feature.txt') as json_file:  
    data = json.load(json_file)
    keys = data.keys()
    for key in keys:
        print(key)
        posts = data[key]
        ids = posts.keys()
        for i in ids:
            print(posts[i])
        

3.0
['-0.263193485', '0.040504625', '-0.077210643', '0.376023312', '-0.126799685', '0.292204925', '-0.057926305', '0.160891639', '-0.101574483', '0.088706719', '0.219812377', '0.041306027', '0.045448225', '0.18278806', '-0.096411438', '0.201370577', '-0.208626641', '0.154250852', '-0.024330153', '-0.263783538', '-0.121470101', '0.037513885', '0.121071604', '-0.061459715', '0.070752093', '-0.012086583', '0.027024085', '0.506861724', '-0.107107484', '-0.054583098', '0.213862325', '-0.049278643', '1518307200.0']
['-0.149004585', '0.055345142', '-0.09362818', '0.344696351', '-0.181859085', '0.238997673', '-0.036274548', '0.177488352', '-0.114483056', '-0.04524187', '0.158712666', '0.094007174', '0.250078598', '0.180163318', '-0.061849335', '0.192400132', '-0.228342417', '0.109870081', '-0.139372158', '-0.32185335', '-0.14464301', '0.077789847', '0.169287356', '-0.161980134', '0.055205098', '0.109419924', '0.078493406', '0.440681913', '-0.044245789', '-0.049794264', '0.200269559', '-0.10049

['-0.376045534', '0.287381114', '-0.000705624', '-0.05237967', '0.14044155', '0.083752071', '0.010650786', '0.307196966', '-0.00027642', '0.216789358', '0.033866889', '-0.077886181', '0.024464271', '0.070382284', '-0.39529325', '-0.010013029', '-0.338124415', '0.052152765', '-0.199547806', '0.062173041', '0.246129327', '0.170885449', '0.124119549', '-0.055645353', '0.047916569', '0.191164778', '-0.012566352', '0.102642685', '-0.148289339', '-0.059294781', '0.020084542', '-0.302418878', '1350950400.0']
['-0.348978465', '0.140993337', '-0.104535419', '-0.040623379', '0.039568037', '0.054119184', '0.025156721', '0.118097548', '0.096541976', '0.098784091', '-0.076260794', '0.043098372', '-0.119755081', '0.05369192', '-0.485663835', '-0.20835812', '-0.170164157', '0.095286136', '-0.168245393', '-0.062053557', '0.118892435', '0.188006996', '0.229243767', '0.020883561', '-0.07070276', '0.313736599', '-0.0631925', '0.027372596', '-0.151214064', '-0.064211514', '0.166278097', '-0.409818958', '1

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




['-0.0353589', '0.07390724', '-0.183253682', '-0.01125667', '0.022568478', '0.063177324', '-0.255238845', '-0.002319672', '0.01543519', '0.024887608', '-0.165773018', '0.150796228', '-0.094380125', '0.182492811', '-0.216587871', '-0.250196311', '-0.242926464', '-0.194842429', '-0.203758488', '-0.235737567', '0.255225987', '0.069368575', '0.050643228', '-0.220561376', '-0.097867803', '0.288659289', '0.172767617', '0.146084728', '-0.040928634', '-0.065193947', '0.284752452', '-0.375228386', '1477267200.0']
['-0.120623819', '-0.081134511', '-0.051659256', '0.061251549', '0.154309928', '0.122564151', '-0.222781676', '0.046174579', '-0.049507608', '0.017923922', '-0.030166952', '0.184489694', '-0.099778282', '0.230291582', '-0.278173432', '-0.15642699', '-0.255996233', '-0.108934192', '-0.203256364', '-0.323541696', '0.345520761', '0.081777232', '0.093882404', '-0.019816525', '-0.088922664', '0.259904427', '0.179080261', '0.112996089', '-0.047254825', '-0.114648074', '0.330800592', '-0.274

['-0.008462829', '-0.101651119', '-0.088764226', '0.173251736', '0.124243121', '0.005996016', '0.141019406', '0.322169849', '0.078586551', '0.325549217', '0.09380649', '0.03007309', '-0.168355619', '0.257242211', '-0.291397948', '-0.100378813', '0.193318449', '-0.131623106', '0.049957112', '0.070161014', '0.089228547', '-0.130239848', '-0.223415433', '-0.037297018', '0.184752571', '0.388897779', '0.104048379', '-0.089318339', '-0.176694105', '0.055752427', '0.167621393', '-0.310210321', '1343952000.0']
['0.079007882', '0.030237256', '0.011203161', '0.217389252', '0.128275096', '-0.017032868', '0.084269954', '0.408268665', '0.032607185', '0.338689661', '0.110980767', '0.030556653', '-0.125624719', '0.254437864', '-0.305998846', '-0.129929077', '0.074125862', '-0.034101857', '0.019096223', '0.075468748', '0.078297887', '-0.067077251', '-0.135456782', '-0.065414127', '0.094441999', '0.404550339', '0.159825028', '-0.071464617', '-0.186667399', '-0.045201876', '0.147659405', '-0.356330099',

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [52]:
def f(x):
    d = tuple()
    for i in range(len(x)):
        if i == 0:
            d += (x[i],)
        else:
            d += (float(x[i]),)
    return d

#Now populate that
df = post_feature.map(lambda x: f(x)).toDF()
df.show(1)

+-------+------------+-----------+------------+-----------+------------+-----------+----------+-----------+------------+-----------+-----------+-----------+-----------+-----------+----------+-----------+------------+-----------+-----------+------------+------------+-----------+-----------+------------+-----------+---------+-----------+-----------+------------+-----------+-----------+------------+-----------+
|     _1|          _2|         _3|          _4|         _5|          _6|         _7|        _8|         _9|         _10|        _11|        _12|        _13|        _14|        _15|       _16|        _17|         _18|        _19|        _20|         _21|         _22|        _23|        _24|         _25|        _26|      _27|        _28|        _29|         _30|        _31|        _32|         _33|        _34|
+-------+------------+-----------+------------+-----------+------------+-----------+----------+-----------+------------+-----------+-----------+-----------+-----------+--------

In [53]:
df.write.csv('post_feature_val_test')